In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from matplotlib.animation import FuncAnimation
import seaborn as sns
from scipy import stats

In [ ]:
def parse_probability(prob_str):
    if isinstance(prob_str, (int, float)):
        return prob_str / 100 if prob_str > 1 else prob_str
    elif pd.isna(prob_str) or not isinstance(prob_str, str):
        return 0
    else:
        return float(prob_str.strip('%')) / 100


def simulate_summons(game_name, num_rolls, base_ssr_rate, rate_up_ssr_rate, guarantee, pity_threshold, pity_increment):
    # Parse probabilities and parameters
    base_ssr_rate = parse_probability(base_ssr_rate)
    rate_up_ssr_rate = parse_probability(rate_up_ssr_rate)
    pity_increment = parse_probability(pity_increment)

    # Initialize counters
    ssr_count = 0
    specific_ssr_count = 0
    current_pity = 0

    for roll in range(num_rolls):
        # Check and apply pity system
        if pity_threshold and roll >= pity_threshold:
            adjusted_ssr_rate = min(base_ssr_rate + current_pity, 1)
            adjusted_rate_up_ssr_rate = min(rate_up_ssr_rate + current_pity, adjusted_ssr_rate)
        else:
            adjusted_ssr_rate = base_ssr_rate
            adjusted_rate_up_ssr_rate = rate_up_ssr_rate

        # Simulate the roll
        roll_result = np.random.random()
        if roll_result < adjusted_ssr_rate:
            ssr_count += 1
            current_pity = 0  # Reset pity increment after an SSR is summoned
            if roll_result < adjusted_rate_up_ssr_rate:
                specific_ssr_count += 1
        else:
            # Increment pity only if SSR is not summoned
            if pity_threshold and roll >= pity_threshold:
                current_pity += pity_increment

        # Check and apply guarantee system
        if guarantee and roll >= guarantee:
            specific_ssr_count += 1
            ssr_count += 1
            break

    return ssr_count, specific_ssr_count


# Example of using the function for a single game with hypothetical parameters
simulate_summons("Example Game", 100, "2%", "0.7%", None, 50, "2%")

In [ ]:
gacha_data = pd.read_csv("gacha.csv")
print(gacha_data.head())

In [ ]:
def convert_to_int(val):
    try:
        return int(val)
    except (ValueError, TypeError):
        return None

results = []

for index, row in gacha_data.iterrows():
    game_name = row['Unnamed: 0']  
    base_ssr_rate = row['Base SSR rate']
    rate_up_ssr_rate = row['Specific rate-up SSR rate']
    guarantee = convert_to_int(row['Specific unit guarantee'])
    pity_threshold = convert_to_int(row['Pity after X rolls'])
    pity_increment = row['Pity increment (per roll)']

    num_rolls = 300  # Set the number of rolls for simulation

    ssr_count, specific_ssr_count = simulate_summons(
        game_name, num_rolls, base_ssr_rate, rate_up_ssr_rate, 
        guarantee, pity_threshold, pity_increment
    )

    results.append([game_name, ssr_count, specific_ssr_count])

simulation_results = pd.DataFrame(results, columns=['Game', 'SSR Count', 'Specific SSR Count'])


In [ ]:
# Example: Basic summary statistics
summary_stats = simulation_results.describe()
print(summary_stats)

In [ ]:
plt.figure(figsize=(10, 6))
sns.barplot(x='Game', y='SSR Count', data=simulation_results)
plt.title('SSR Count per Game')
plt.xticks(rotation=45)
plt.show()